# Train LGBMRegressor(tuned) + catboost(default) + combined dataset + 10 split fold + labeled datasources + distance to cities

# Imports

In [1]:
!pip install polars

In [2]:
!pip install snoop

In [3]:
import polars as pl
from snoop import pp
from polars.testing import assert_frame_equal, assert_series_equal

In [4]:
import pandas as pd
from pathlib import Path
import numpy as np

In [5]:
from IPython.core.interactiveshell import InteractiveShell
InteractiveShell.ast_node_interactivity = "all"

In [9]:
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler, MinMaxScaler
from sklearn.metrics import mean_squared_error
from sklearn import metrics
from sklearn.svm import SVR
from sklearn.datasets import fetch_california_housing

In [10]:
class Data:
    def __init__(self, data_type: str = 'train', scaler_type: str = 'minmax', use_original_data=False):
        self.data_type = data_type
        self.data = pd.read_csv('train.csv', index_col=0) if data_type == 'train' else pd.read_csv('test.csv',
                                                                                                   index_col=0)
        self.scaler_type = scaler_type
        self.use_original_data = use_original_data

        if self.data_type == 'train':
            self.processed_data = self.process_data(self.data, scaler_type=scaler_type, handle_last_col=False)
        if self.data_type == 'test':
            self.processed_data = self.process_data(self.data, scaler_type=scaler_type, handle_last_col=True)

        if self.use_original_data:
            self.data = self.add_raw_data_to_train(self.data)

    @staticmethod
    def add_raw_data_to_train(df):
        original_df = fetch_california_housing()['data']
        original_df_train = pd.DataFrame(original_df, columns=fetch_california_housing()['feature_names'])
        original_df_train['MedHouseVal'] = fetch_california_housing()['target']
        return pd.concat([df, original_df_train], axis=0)

    @staticmethod
    def process_data(df, scaler_type='minmax', handle_last_col=True):
        raw_cols = df.columns
        raw_index = df.index
        if scaler_type == 'minmax':
            # use minmax scaler
            scaler = MinMaxScaler()

            if handle_last_col:
                # handle all columns
                return pd.DataFrame(scaler.fit_transform(df), columns=raw_cols, index=raw_index)
            else:
                # use the original last column
                return pd.DataFrame(scaler.fit_transform(df.iloc[:, :-1]), columns=raw_cols[:-1], index=raw_index).join(
                    df.iloc[:, -1])

        elif scaler_type == 'standard':
            # use standard scaler
            scaler = StandardScaler()
            # use the original last column

            if handle_last_col:
                # handle all columns
                return pd.DataFrame(scaler.fit_transform(df), columns=raw_cols, index=raw_index)
            else:
                return pd.DataFrame(scaler.fit_transform(df.iloc[:, :-1]), columns=raw_cols[:-1], index=raw_index). \
                    join(df.iloc[:, -1])

        elif scaler_type == 'none':
            return df

    def get_train_test_split(self, test_size: float = 0.3, random_state: int = 42):
        if self.use_original_data:
            raw_train = self.add_raw_data_to_train(pd.read_csv('train.csv', index_col=0))
        else:
            raw_train = pd.read_csv('train.csv', index_col=0)
        processed_train = self.process_data(raw_train, scaler_type=self.scaler_type, handle_last_col=False)

        X = processed_train.drop('MedHouseVal', axis=1)
        y = processed_train['MedHouseVal']

        x_train, x_test, y_train, y_test = train_test_split(X, y, test_size=test_size, random_state=random_state)
        return x_train, x_test, y_train, y_test

In [11]:
data = Data('train', scaler_type='none', use_original_data=True)

In [12]:
data.data.to_csv('train_added_raw.csv')

In [13]:
train_pl = pl.read_csv('train_added_raw.csv')
test_pl = pl.read_csv('test.csv')
sample_sub_pl = pl.read_csv('sample_submission.csv')

# join Kaggle dataset with SKlearn dataset

In [14]:
from sklearn.datasets import fetch_california_housing

original_data = fetch_california_housing()
original_data.feature_names
original_data.target_names

['MedInc',
 'HouseAge',
 'AveRooms',
 'AveBedrms',
 'Population',
 'AveOccup',
 'Latitude',
 'Longitude']

['MedHouseVal']

In [15]:
additional_data = ( 
    pl.concat([
        pl.from_numpy(original_data.data, original_data.feature_names), 
        pl.from_numpy(original_data.target, original_data.target_names),
    ],how='horizontal')
    .select([
        pl.all().exclude('MedHouseVal'),
        pl.lit(False).alias('is_generated'), # add labels to distinguish two datasets
        'MedHouseVal',
    ])
)
additional_data.head()
additional_data.columns

shape: (5, 10)
┌────────┬──────────┬──────────┬───────────┬─────┬──────────┬───────────┬────────────┬─────────────┐
│ MedInc ┆ HouseAge ┆ AveRooms ┆ AveBedrms ┆ ... ┆ Latitude ┆ Longitude ┆ is_generat ┆ MedHouseVal │
│ ---    ┆ ---      ┆ ---      ┆ ---       ┆     ┆ ---      ┆ ---       ┆ ed         ┆ ---         │
│ f64    ┆ f64      ┆ f64      ┆ f64       ┆     ┆ f64      ┆ f64       ┆ ---        ┆ f64         │
│        ┆          ┆          ┆           ┆     ┆          ┆           ┆ bool       ┆             │
╞════════╪══════════╪══════════╪═══════════╪═════╪══════════╪═══════════╪════════════╪═════════════╡
│ 8.3252 ┆ 41.0     ┆ 6.984127 ┆ 1.02381   ┆ ... ┆ 37.88    ┆ -122.23   ┆ false      ┆ 4.526       │
│ 8.3014 ┆ 21.0     ┆ 6.238137 ┆ 0.97188   ┆ ... ┆ 37.86    ┆ -122.22   ┆ false      ┆ 3.585       │
│ 7.2574 ┆ 52.0     ┆ 8.288136 ┆ 1.073446  ┆ ... ┆ 37.85    ┆ -122.24   ┆ false      ┆ 3.521       │
│ 5.6431 ┆ 52.0     ┆ 5.817352 ┆ 1.073059  ┆ ... ┆ 37.85    ┆ -122.25   ┆ false      ┆ 3.413       │
│ 3.8462 ┆ 52.0     ┆ 6.281853 ┆ 1.081081  ┆ ... ┆ 37.85    ┆ -122.25   ┆ false      ┆ 3.422       │
└────────┴──────────┴──────────┴───────────┴─────┴──────────┴───────────┴────────────┴─────────────┘

['MedInc',
 'HouseAge',
 'AveRooms',
 'AveBedrms',
 'Population',
 'AveOccup',
 'Latitude',
 'Longitude',
 'is_generated',
 'MedHouseVal']

In [16]:
train_pl = (
    train_pl
    .select([
        pl.all().exclude('MedHouseVal'),
        pl.lit(True).alias('is_generated'),
        'MedHouseVal',
    ])
)
train_pl.head()


shape: (5, 11)
┌─────┬────────┬──────────┬──────────┬─────┬──────────┬───────────┬──────────────┬─────────────┐
│     ┆ MedInc ┆ HouseAge ┆ AveRooms ┆ ... ┆ Latitude ┆ Longitude ┆ is_generated ┆ MedHouseVal │
│ --- ┆ ---    ┆ ---      ┆ ---      ┆     ┆ ---      ┆ ---       ┆ ---          ┆ ---         │
│ i64 ┆ f64    ┆ f64      ┆ f64      ┆     ┆ f64      ┆ f64       ┆ bool         ┆ f64         │
╞═════╪════════╪══════════╪══════════╪═════╪══════════╪═══════════╪══════════════╪═════════════╡
│ 0   ┆ 2.3859 ┆ 15.0     ┆ 3.82716  ┆ ... ┆ 34.6     ┆ -120.12   ┆ true         ┆ 0.98        │
│ 1   ┆ 3.7188 ┆ 17.0     ┆ 6.013373 ┆ ... ┆ 38.69    ┆ -121.22   ┆ true         ┆ 0.946       │
│ 2   ┆ 4.775  ┆ 27.0     ┆ 6.535604 ┆ ... ┆ 34.71    ┆ -120.45   ┆ true         ┆ 1.576       │
│ 3   ┆ 2.4138 ┆ 16.0     ┆ 3.350203 ┆ ... ┆ 32.66    ┆ -117.09   ┆ true         ┆ 1.336       │
│ 4   ┆ 3.75   ┆ 52.0     ┆ 4.284404 ┆ ... ┆ 37.8     ┆ -122.41   ┆ true         ┆ 4.5         │
└─────┴────────┴──────────┴──────────┴─────┴──────────┴───────────┴──────────────┴─────────────┘

In [17]:
features = ['MedInc', 'HouseAge', 'AveRooms', 'AveBedrms', 'Population', 'AveOccup', 'Latitude', 'Longitude', 'is_generated'] # added ext_src
target = 'MedHouseVal'

In [18]:
features + [target]
train_joined_pl = train_pl[features + [target]].vstack(additional_data) # not including column `id`
train_joined_pl.shape
train_joined_pl.columns

['MedInc',
 'HouseAge',
 'AveRooms',
 'AveBedrms',
 'Population',
 'AveOccup',
 'Latitude',
 'Longitude',
 'is_generated',
 'MedHouseVal']

(78417, 10)

['MedInc',
 'HouseAge',
 'AveRooms',
 'AveBedrms',
 'Population',
 'AveOccup',
 'Latitude',
 'Longitude',
 'is_generated',
 'MedHouseVal']

# Feature: distance to cities
Thanks to @phongnguyen1, reference: https://www.kaggle.com/code/phongnguyen1/distance-to-cities-features-clustering?scriptVersionId=115694922&cellId=40

**About haversine_distances** [link](https://scikit-learn.org/stable/modules/generated/sklearn.metrics.pairwise.haversine_distances.html)

> The Haversine (or great circle) distance is the angular distance between two points on the surface of a sphere. The first coordinate of each point is assumed to be the latitude, the second is the longitude, given in radians. The dimension of the data must be 2.

> As the Earth is nearly spherical, the haversine formula provides a good approximation of the distance between two points of the Earth surface, with a less than 1% error on average.

In [19]:
def get_distance(lat1, long1, lat2, long2):
    from sklearn.metrics.pairwise import haversine_distances
    from math import radians

    loc1 = [radians(lat1), radians(long1)]
    loc2 = [radians(lat2), radians(long2)]
    result = haversine_distances([loc1, loc2])
    result * 6371000/1000  # multiply by Earth radius to get kilometers
    return result[0][1]

In [20]:
Sacramento = (38.576931, -121.494949)
SanFrancisco = (37.780080, -122.420160)
SanJose = (37.334789, -121.888138)
LosAngeles = (34.052235, -118.243683)
SanDiego = (32.715759, -117.163818)

In [21]:
train_joined_pl_add_dist = (
    train_joined_pl
    .with_columns([
        pl.struct(['Latitude', 'Longitude']).apply(lambda x: get_distance(x['Latitude'], x['Longitude'], Sacramento[0], Sacramento[1])).alias('dist2Sacramento'),
        pl.struct(['Latitude', 'Longitude']).apply(lambda x: get_distance(x['Latitude'], x['Longitude'], SanFrancisco[0], SanFrancisco[1])).alias('dist2SanFrancisco'),
        pl.struct(['Latitude', 'Longitude']).apply(lambda x: get_distance(x['Latitude'], x['Longitude'], SanJose[0], SanJose[1])).alias('dist2SanJose'),
        pl.struct(['Latitude', 'Longitude']).apply(lambda x: get_distance(x['Latitude'], x['Longitude'], LosAngeles[0], LosAngeles[1])).alias('dist2LosAngeles'),
        pl.struct(['Latitude', 'Longitude']).apply(lambda x: get_distance(x['Latitude'], x['Longitude'], SanDiego[0], SanDiego[1])).alias('dist2SanDiego'),        
    ])
    .with_columns([
        pl.struct(['dist2Sacramento', 'dist2SanFrancisco', 'dist2SanJose', 'dist2LosAngeles', 'dist2SanDiego']).apply(lambda x: min([x['dist2Sacramento'], x['dist2SanFrancisco'], x['dist2SanJose'], x['dist2LosAngeles'], x['dist2SanDiego']])).alias('dist2nearestCity'),
        pl.struct(['dist2Sacramento', 'dist2SanFrancisco', 'dist2SanJose', 'dist2LosAngeles', 'dist2SanDiego']).apply(lambda x: max([x['dist2Sacramento'], x['dist2SanFrancisco'], x['dist2SanJose'], x['dist2LosAngeles'], x['dist2SanDiego']])).alias('dist2furthestCity'),
        pl.struct(['dist2Sacramento', 'dist2SanFrancisco', 'dist2SanJose', 'dist2LosAngeles', 'dist2SanDiego']).apply(lambda x: sum([x['dist2Sacramento'], x['dist2SanFrancisco'], x['dist2SanJose'], x['dist2LosAngeles'], x['dist2SanDiego']])).alias('dist2allCity')        
    ])
)
train_joined_pl_add_dist

shape: (78417, 18)
┌────────┬──────────┬──────────┬───────────┬─────┬────────────┬────────────┬────────────┬────────────┐
│ MedInc ┆ HouseAge ┆ AveRooms ┆ AveBedrms ┆ ... ┆ dist2SanDi ┆ dist2neare ┆ dist2furth ┆ dist2allCi │
│ ---    ┆ ---      ┆ ---      ┆ ---       ┆     ┆ ego        ┆ stCity     ┆ estCity    ┆ ty         │
│ f64    ┆ f64      ┆ f64      ┆ f64       ┆     ┆ ---        ┆ ---        ┆ ---        ┆ ---        │
│        ┆          ┆          ┆           ┆     ┆ f64        ┆ f64        ┆ f64        ┆ f64        │
╞════════╪══════════╪══════════╪═══════════╪═════╪════════════╪════════════╪════════════╪════════════╡
│ 2.3859 ┆ 15.0     ┆ 3.82716  ┆ 1.1121    ┆ ... ┆ 0.054086   ┆ 0.028684   ┆ 0.072033   ┆ 0.272933   │
│ 3.7188 ┆ 17.0     ┆ 6.013373 ┆ 1.054217  ┆ ... ┆ 0.119034   ┆ 0.004236   ┆ 0.119034   ┆ 0.262609   │
│ 4.775  ┆ 27.0     ┆ 6.535604 ┆ 1.103175  ┆ ... ┆ 0.05905    ┆ 0.033789   ┆ 0.069057   ┆ 0.272332   │
│ 2.4138 ┆ 16.0     ┆ 3.350203 ┆ 0.965432  ┆ ... ┆ 0.001457   ┆ 0.001457   ┆ 0.12067    ┆ 0.375504   │
│ ...    ┆ ...      ┆ ...      ┆ ...       ┆ ... ┆ ...        ┆ ...        ┆ ...        ┆ ...        │
│ 2.5568 ┆ 18.0     ┆ 6.114035 ┆ 1.315789  ┆ ... ┆ 0.131241   ┆ 0.016398   ┆ 0.131241   ┆ 0.324035   │
│ 1.7    ┆ 17.0     ┆ 5.205543 ┆ 1.120092  ┆ ... ┆ 0.13037    ┆ 0.015349   ┆ 0.13037    ┆ 0.319195   │
│ 1.8672 ┆ 18.0     ┆ 5.329513 ┆ 1.17192   ┆ ... ┆ 0.130994   ┆ 0.015077   ┆ 0.130994   ┆ 0.319159   │
│ 2.3886 ┆ 16.0     ┆ 5.254717 ┆ 1.162264  ┆ ... ┆ 0.129565   ┆ 0.014267   ┆ 0.129565   ┆ 0.314351   │
└────────┴──────────┴──────────┴───────────┴─────┴────────────┴────────────┴────────────┴────────────┘

In [22]:
features = (train_joined_pl_add_dist.columns)

features.remove('MedHouseVal')

features, target
len(features)

(['MedInc',
  'HouseAge',
  'AveRooms',
  'AveBedrms',
  'Population',
  'AveOccup',
  'Latitude',
  'Longitude',
  'is_generated',
  'dist2Sacramento',
  'dist2SanFrancisco',
  'dist2SanJose',
  'dist2LosAngeles',
  'dist2SanDiego',
  'dist2nearestCity',
  'dist2furthestCity',
  'dist2allCity'],
 'MedHouseVal')

17

# Training LGBMRegressor model

Let's begin by splitting our data into a train and validation set.

In [23]:
from lightgbm.sklearn import LGBMRegressor
import lightgbm as lgbm
from sklearn.metrics import mean_squared_error
from sklearn.model_selection import KFold

The variable that we will be predicting is the `MedHouseVal`. We will use the rest of the columns (minus the id column) for training.

In [24]:
# these parameters come from soupmonsters awesome notebook here: https://www.kaggle.com/code/soupmonster/simple-lightgbm-baseline
params= {
 'learning_rate': 0.02, 
 'n_estimators': 100_000, 
 'metric': 'rmse',
 'lambda_l1': 1.945,
 'num_leaves': 87,
 'feature_fraction': 0.79,
 'bagging_fraction': 0.93,
 'bagging_freq': 4,
 'min_data_in_leaf': 103,
 'max_depth': 17,
}

In [25]:
clfs_f64pl = []
kf = KFold(n_splits=10, random_state=0, shuffle=True) # this line must be included in the same cell as the training block below
rmses = []

for i, (train_index, val_index) in enumerate(kf.split(train_joined_pl_add_dist)): # kf.split can work with pl.DataFrame
    X_train, X_val = train_joined_pl_add_dist[features][train_index].select(pl.all().cast(pl.Float64)), train_joined_pl_add_dist[features][val_index].select(pl.all().cast(pl.Float64))
    y_train, y_val = train_joined_pl_add_dist[target][train_index].cast(pl.Float64), train_joined_pl_add_dist[target][val_index].cast(pl.Float64)

    clf = LGBMRegressor(**params)
    clf.fit(X_train.to_numpy(),
            y_train.to_numpy(),
            eval_set=[(X_val.to_numpy(), y_val.to_numpy())], 
            callbacks=[lgbm.early_stopping(85, verbose=True)]) # why early_stop at 500 

    preds = clf.predict(X_val.to_numpy())
    
    clfs_f64pl.append(clf) # save 5 trained models into this list
    rmses.append(mean_squared_error(y_val.to_numpy(), preds, squared=False))
    
print(f'mean RMSE across all folds: {pl.Series(rmses).mean()}')

[LightGBM] [Warning] min_data_in_leaf is set=103, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=103
[LightGBM] [Warning] bagging_fraction is set=0.93, subsample=1.0 will be ignored. Current value: bagging_fraction=0.93
[LightGBM] [Warning] feature_fraction is set=0.79, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.79
[LightGBM] [Warning] bagging_freq is set=4, subsample_freq=0 will be ignored. Current value: bagging_freq=4
[LightGBM] [Warning] lambda_l1 is set=1.945, reg_alpha=0.0 will be ignored. Current value: lambda_l1=1.945
[1]	valid_0's rmse: 1.14643
Training until validation scores don't improve for 85 rounds
[2]	valid_0's rmse: 1.13041
[3]	valid_0's rmse: 1.11599
[4]	valid_0's rmse: 1.10063
[5]	valid_0's rmse: 1.08576
[6]	valid_0's rmse: 1.0711
[7]	valid_0's rmse: 1.05779
[8]	valid_0's rmse: 1.04482
[9]	valid_0's rmse: 1.0313
[10]	valid_0's rmse: 1.01813
[11]	valid_0's rmse: 1.00481
[12]	valid_0's rmse: 0.992086
[13]	valid_0's rm

LGBMRegressor(bagging_fraction=0.93, bagging_freq=4, feature_fraction=0.79,
              lambda_l1=1.945, learning_rate=0.02, max_depth=17, metric='rmse',
              min_data_in_leaf=103, n_estimators=100000, num_leaves=87)

[LightGBM] [Warning] min_data_in_leaf is set=103, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=103
[LightGBM] [Warning] bagging_fraction is set=0.93, subsample=1.0 will be ignored. Current value: bagging_fraction=0.93
[LightGBM] [Warning] feature_fraction is set=0.79, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.79
[LightGBM] [Warning] bagging_freq is set=4, subsample_freq=0 will be ignored. Current value: bagging_freq=4
[LightGBM] [Warning] lambda_l1 is set=1.945, reg_alpha=0.0 will be ignored. Current value: lambda_l1=1.945
[1]	valid_0's rmse: 1.13745
Training until validation scores don't improve for 85 rounds
[2]	valid_0's rmse: 1.12145
[3]	valid_0's rmse: 1.10696
[4]	valid_0's rmse: 1.09157
[5]	valid_0's rmse: 1.07673
[6]	valid_0's rmse: 1.0622
[7]	valid_0's rmse: 1.04863
[8]	valid_0's rmse: 1.03561
[9]	valid_0's rmse: 1.02213
[10]	valid_0's rmse: 1.00885
[11]	valid_0's rmse: 0.995823
[12]	valid_0's rmse: 0.983184
[13]	valid_0's 

LGBMRegressor(bagging_fraction=0.93, bagging_freq=4, feature_fraction=0.79,
              lambda_l1=1.945, learning_rate=0.02, max_depth=17, metric='rmse',
              min_data_in_leaf=103, n_estimators=100000, num_leaves=87)

[LightGBM] [Warning] min_data_in_leaf is set=103, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=103
[LightGBM] [Warning] bagging_fraction is set=0.93, subsample=1.0 will be ignored. Current value: bagging_fraction=0.93
[LightGBM] [Warning] feature_fraction is set=0.79, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.79
[LightGBM] [Warning] bagging_freq is set=4, subsample_freq=0 will be ignored. Current value: bagging_freq=4
[LightGBM] [Warning] lambda_l1 is set=1.945, reg_alpha=0.0 will be ignored. Current value: lambda_l1=1.945
[1]	valid_0's rmse: 1.13733
Training until validation scores don't improve for 85 rounds
[2]	valid_0's rmse: 1.12117
[3]	valid_0's rmse: 1.10657
[4]	valid_0's rmse: 1.09108
[5]	valid_0's rmse: 1.07606
[6]	valid_0's rmse: 1.06129
[7]	valid_0's rmse: 1.04774
[8]	valid_0's rmse: 1.03461
[9]	valid_0's rmse: 1.0211
[10]	valid_0's rmse: 1.00776
[11]	valid_0's rmse: 0.994672
[12]	valid_0's rmse: 0.981911
[13]	valid_0's 

...

[LightGBM] [Warning] min_data_in_leaf is set=103, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=103
[LightGBM] [Warning] bagging_fraction is set=0.93, subsample=1.0 will be ignored. Current value: bagging_fraction=0.93
[LightGBM] [Warning] feature_fraction is set=0.79, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.79
[LightGBM] [Warning] bagging_freq is set=4, subsample_freq=0 will be ignored. Current value: bagging_freq=4
[LightGBM] [Warning] lambda_l1 is set=1.945, reg_alpha=0.0 will be ignored. Current value: lambda_l1=1.945
[1]	valid_0's rmse: 1.1422
Training until validation scores don't improve for 85 rounds
[2]	valid_0's rmse: 1.12632
[3]	valid_0's rmse: 1.1122
[4]	valid_0's rmse: 1.09712
[5]	valid_0's rmse: 1.08224
[6]	valid_0's rmse: 1.0677
[7]	valid_0's rmse: 1.05438
[8]	valid_0's rmse: 1.04137
[9]	valid_0's rmse: 1.02805
[10]	valid_0's rmse: 1.01492
[11]	valid_0's rmse: 1.00196
[12]	valid_0's rmse: 0.989207
[13]	valid_0's rms

LGBMRegressor(bagging_fraction=0.93, bagging_freq=4, feature_fraction=0.79,
              lambda_l1=1.945, learning_rate=0.02, max_depth=17, metric='rmse',
              min_data_in_leaf=103, n_estimators=100000, num_leaves=87)

[LightGBM] [Warning] min_data_in_leaf is set=103, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=103
[LightGBM] [Warning] bagging_fraction is set=0.93, subsample=1.0 will be ignored. Current value: bagging_fraction=0.93
[LightGBM] [Warning] feature_fraction is set=0.79, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.79
[LightGBM] [Warning] bagging_freq is set=4, subsample_freq=0 will be ignored. Current value: bagging_freq=4
[LightGBM] [Warning] lambda_l1 is set=1.945, reg_alpha=0.0 will be ignored. Current value: lambda_l1=1.945
[1]	valid_0's rmse: 1.14644
Training until validation scores don't improve for 85 rounds
[2]	valid_0's rmse: 1.13041
[3]	valid_0's rmse: 1.11599
[4]	valid_0's rmse: 1.10049
[5]	valid_0's rmse: 1.08555
[6]	valid_0's rmse: 1.07094
[7]	valid_0's rmse: 1.05745
[8]	valid_0's rmse: 1.04451
[9]	valid_0's rmse: 1.03106
[10]	valid_0's rmse: 1.01778
[11]	valid_0's rmse: 1.00484
[12]	valid_0's rmse: 0.992215
[13]	valid_0's 

LGBMRegressor(bagging_fraction=0.93, bagging_freq=4, feature_fraction=0.79,
              lambda_l1=1.945, learning_rate=0.02, max_depth=17, metric='rmse',
              min_data_in_leaf=103, n_estimators=100000, num_leaves=87)

mean RMSE across all folds: 0.42904179521301045


# Train a catboost model

In [26]:
from catboost import CatBoostRegressor
clfs_f64pl_cat = []
rmses = []
kf = KFold(n_splits=10, random_state=1, shuffle=True)
for train_index, val_index in kf.split(train_joined_pl_add_dist):
    X_train = train_joined_pl_add_dist[features][train_index].select(pl.all().cast(pl.Float64))
    X_val = train_joined_pl_add_dist[features][val_index].select(pl.all().cast(pl.Float64))
    y_train = train_joined_pl_add_dist[target][train_index].cast(pl.Float64)
    y_val = train_joined_pl_add_dist[target][val_index].cast(pl.Float64)

    clf = CatBoostRegressor(iterations=100_000, loss_function='RMSE')
    clf.fit(X_train.to_numpy(),
            y_train.to_numpy(),
            eval_set=(X_val.to_numpy(), y_val.to_numpy()),
            early_stopping_rounds=1000, verbose=False)

    preds = clf.predict(X_val.to_numpy())

    clfs_f64pl_cat.append(clf)
    rmses.append(mean_squared_error(y_val.to_numpy(), preds, squared=False))
print(f'mean RMSE across all folds: {np.mean(rmses)}')

mean RMSE across all folds: 0.4356248721244428


Let us now look at the variables that are important according to our model.

In [27]:
(
    pl.DataFrame({
    "features": features,
    "importance": clf.feature_importances_, # using the latest model
    })
    .with_columns([
        (pl.col('importance')/pl.col('importance').sum()).alias('ratio')
    ])
    .sort('ratio', reverse=True)
)

shape: (17, 3)
┌──────────────────┬────────────┬──────────┐
│ features         ┆ importance ┆ ratio    │
│ ---              ┆ ---        ┆ ---      │
│ str              ┆ f64        ┆ f64      │
╞══════════════════╪════════════╪══════════╡
│ MedInc           ┆ 28.165776  ┆ 0.281658 │
│ AveOccup         ┆ 11.746715  ┆ 0.117467 │
│ dist2nearestCity ┆ 9.821343   ┆ 0.098213 │
│ Longitude        ┆ 9.040001   ┆ 0.0904   │
│ ...              ┆ ...        ┆ ...      │
│ dist2allCity     ┆ 2.186986   ┆ 0.02187  │
│ dist2SanJose     ┆ 2.03775    ┆ 0.020377 │
│ dist2SanDiego    ┆ 1.338105   ┆ 0.013381 │
│ is_generated     ┆ 0.164851   ┆ 0.001649 │
└──────────────────┴────────────┴──────────┘

# prepare test set

In [28]:
features

['MedInc',
 'HouseAge',
 'AveRooms',
 'AveBedrms',
 'Population',
 'AveOccup',
 'Latitude',
 'Longitude',
 'is_generated',
 'dist2Sacramento',
 'dist2SanFrancisco',
 'dist2SanJose',
 'dist2LosAngeles',
 'dist2SanDiego',
 'dist2nearestCity',
 'dist2furthestCity',
 'dist2allCity']

In [29]:
test_pl_adddist = (

    test_pl
    .select([
        pl.all(),
        pl.lit(True).alias('is_generated'),
    ])
    .with_columns([
        pl.struct(['Latitude', 'Longitude']).apply(lambda x: get_distance(x['Latitude'], x['Longitude'], Sacramento[0], Sacramento[1])).alias('dist2Sacramento'),
        pl.struct(['Latitude', 'Longitude']).apply(lambda x: get_distance(x['Latitude'], x['Longitude'], SanFrancisco[0], SanFrancisco[1])).alias('dist2SanFrancisco'),
        pl.struct(['Latitude', 'Longitude']).apply(lambda x: get_distance(x['Latitude'], x['Longitude'], SanJose[0], SanJose[1])).alias('dist2SanJose'),
        pl.struct(['Latitude', 'Longitude']).apply(lambda x: get_distance(x['Latitude'], x['Longitude'], LosAngeles[0], LosAngeles[1])).alias('dist2LosAngeles'),
        pl.struct(['Latitude', 'Longitude']).apply(lambda x: get_distance(x['Latitude'], x['Longitude'], SanDiego[0], SanDiego[1])).alias('dist2SanDiego'),        
    ])
    .with_columns([
        pl.struct(['dist2Sacramento', 'dist2SanFrancisco', 'dist2SanJose', 'dist2LosAngeles', 'dist2SanDiego']).apply(lambda x: min([x['dist2Sacramento'], x['dist2SanFrancisco'], x['dist2SanJose'], x['dist2LosAngeles'], x['dist2SanDiego']])).alias('dist2nearestCity'),
        pl.struct(['dist2Sacramento', 'dist2SanFrancisco', 'dist2SanJose', 'dist2LosAngeles', 'dist2SanDiego']).apply(lambda x: max([x['dist2Sacramento'], x['dist2SanFrancisco'], x['dist2SanJose'], x['dist2LosAngeles'], x['dist2SanDiego']])).alias('dist2furthestCity'),
        pl.struct(['dist2Sacramento', 'dist2SanFrancisco', 'dist2SanJose', 'dist2LosAngeles', 'dist2SanDiego']).apply(lambda x: sum([x['dist2Sacramento'], x['dist2SanFrancisco'], x['dist2SanJose'], x['dist2LosAngeles'], x['dist2SanDiego']])).alias('dist2allCity')        
    ])
)
test_pl_adddist

shape: (24759, 18)
┌───────┬────────┬──────────┬──────────┬─────┬────────────┬────────────┬────────────┬──────────────┐
│ id    ┆ MedInc ┆ HouseAge ┆ AveRooms ┆ ... ┆ dist2SanDi ┆ dist2neare ┆ dist2furth ┆ dist2allCity │
│ ---   ┆ ---    ┆ ---      ┆ ---      ┆     ┆ ego        ┆ stCity     ┆ estCity    ┆ ---          │
│ i64   ┆ f64    ┆ f64      ┆ f64      ┆     ┆ ---        ┆ ---        ┆ ---        ┆ f64          │
│       ┆        ┆          ┆          ┆     ┆ f64        ┆ f64        ┆ f64        ┆              │
╞═══════╪════════╪══════════╪══════════╪═════╪════════════╪════════════╪════════════╪══════════════╡
│ 37137 ┆ 1.7062 ┆ 35.0     ┆ 4.966368 ┆ ... ┆ 0.13932    ┆ 0.02103    ┆ 0.13932    ┆ 0.349183     │
│ 37138 ┆ 1.3882 ┆ 22.0     ┆ 4.187035 ┆ ... ┆ 0.027087   ┆ 0.001906   ┆ 0.09248    ┆ 0.288281     │
│ 37139 ┆ 7.7197 ┆ 21.0     ┆ 7.129436 ┆ ... ┆ 0.018241   ┆ 0.009955   ┆ 0.10105    ┆ 0.31411      │
│ 37140 ┆ 4.6806 ┆ 49.0     ┆ 4.769697 ┆ ... ┆ 0.03062    ┆ 0.002482   ┆ 0.088763   ┆ 0.2819       │
│ ...   ┆ ...    ┆ ...      ┆ ...      ┆ ... ┆ ...        ┆ ...        ┆ ...        ┆ ...          │
│ 61892 ┆ 3.0781 ┆ 33.0     ┆ 4.771971 ┆ ... ┆ 0.026643   ┆ 0.004154   ┆ 0.092733   ┆ 0.293015     │
│ 61893 ┆ 2.6961 ┆ 14.0     ┆ 4.59396  ┆ ... ┆ 0.098676   ┆ 0.014982   ┆ 0.098676   ┆ 0.22746      │
│ 61894 ┆ 7.2315 ┆ 8.0      ┆ 7.508403 ┆ ... ┆ 0.020481   ┆ 0.007688   ┆ 0.098924   ┆ 0.307167     │
│ 61895 ┆ 5.726  ┆ 30.0     ┆ 6.0      ┆ ... ┆ 0.118632   ┆ 0.003214   ┆ 0.118632   ┆ 0.24316      │
└───────┴────────┴──────────┴──────────┴─────┴────────────┴────────────┴────────────┴──────────────┘

# Ensemble 

In [30]:
test_preds = []

for clf in (clfs_f64pl + clfs_f64pl_cat):
    preds = clf.predict(test_pl_adddist[features].to_numpy())
    test_preds.append(preds)

test_preds_mean_pl = (
    pl.DataFrame(test_preds)
    .transpose()
    .select([
        pl.all().explode()
    ])
    .mean(axis=1)
    .to_list()
)

# Make a submission

In [31]:
submission = pl.DataFrame({
    'id': test_pl.select('id').to_series(),
    'MedHouseVal': test_preds_mean_pl
})
# submission.head()

submission.write_csv('clfs_lgbm_cat_extsrc.csv')

This is shaping up to be a very excting challenge! 🥳 

**If you found this notebook useful, please upvote! 🙏 Thank you!**

All the best in the competition!

In [26]:
60/555

0.10810810810810811